#### 在不同地區及溫度下，是否會促進酸雨的形成物質(NOx、SO2)的濃度提升?
- 地區：下拉式選單
- 時間：X軸
- 溫度：Y軸
- 空氣指標(NOx、SO2)：泡泡大小+顏色
    - 濃度用泡泡大小表示
    - 不同指標用不同顏色

In [2]:
import pandas as pd

In [3]:
df = pd.read_csv('./rawData/空氣品質監測月值.csv')

new_col_names = {'"siteid"':'siteid', '"sitename"':'sitename', '"itemid"':'itemid', '"itemname"':'itemname', 
                '"itemengname"':'itemengname', '"itemunit"':'itemunit', '"monitormonth"':'monitormonth', '"concentration"':'concentration'}
df = df.rename(columns=new_col_names)
df

siteid sitename  itemid itemname itemengname itemunit  monitormonth   
0           71       復興       6     一氧化氮          NO      ppb        201101  \
1           38       崙背       6     一氧化氮          NO      ppb        201101   
2           38       崙背       7     二氧化氮         NO2      ppb        201101   
3           11       士林      10       風速  WIND_SPEED    m/sec        201101   
4           49       仁武       8   總碳氫化合物         THC      ppm        201101   
...        ...      ...     ...      ...         ...      ...           ...   
157911      85       大城      14       溫度    AMB_TEMP        ℃        202302   
157912      85       大城      31       甲烷         CH4      ppm        202302   
157913      85       大城      33    細懸浮微粒       PM2.5    μg/m3        202302   
157914      85       大城      38     相對濕度          RH        %        202302   
157915      85       大城     143    小時風速值       WS_HR    m/sec        202302   

       concentration  
0               17.1  
1               3.44  
2              13.33  
3               2.39  
4              2.253  
...              ...  
157911          16.9  
157912          2.02  
157913            19  
157914            85  
157915           6.4  

[157916 rows x 8 columns]

In [4]:
# 溫度、NOx、SO2
df = df[df['itemengname'].isin(['NOx', 'SO2', 'AMB_TEMP'])]
df

siteid sitename  itemid itemname itemengname itemunit  monitormonth   
7           38       崙背      14       溫度    AMB_TEMP        ℃        201101  \
20          11       士林      14       溫度    AMB_TEMP        ℃        201101   
23          39       新港       1     二氧化硫         SO2      ppb        201101   
25          49       仁武       5     氮氧化物         NOx      ppb        201101   
33          39       新港       5     氮氧化物         NOx      ppb        201101   
...        ...      ...     ...      ...         ...      ...           ...   
157890      84      富貴角       5     氮氧化物         NOx      ppb        202302   
157896      84      富貴角      14       溫度    AMB_TEMP        ℃        202302   
157901      85       大城       1     二氧化硫         SO2      ppb        202302   
157905      85       大城       5     氮氧化物         NOx      ppb        202302   
157911      85       大城      14       溫度    AMB_TEMP        ℃        202302   

       concentration  
7              14.98  
20             14.31  
23               3.3  
25             40.62  
33             16.07  
...              ...  
157890           3.1  
157896          15.5  
157901           0.9  
157905           6.6  
157911          16.9  

[33337 rows x 8 columns]

In [62]:
# 取測站位置資料
site_df = pd.read_csv('./rawData/監測站基本資料.csv')
merged_df = df.merge(site_df[['sitename', 'areaname', 'county']], on='sitename')


merged_df['concentration'] = pd.to_numeric(merged_df['concentration'], errors='coerce')
print(merged_df.dtypes['concentration'])

# 日期格式處理
merged_df['monitormonth'] = merged_df['monitormonth'].astype(str)
merged_df[['year', 'month']] = merged_df['monitormonth'].str.extract(r'(.{4})(.*)')
merged_df['monitormonth'] = pd.to_datetime(merged_df['year'].astype(str) + '-' + merged_df['month'].astype(str), format='%Y-%m')
merged_df['monitormonth'] = merged_df['monitormonth'].dt.strftime('%Y/%m')

merged_df

float64


siteid sitename  itemid itemname itemengname itemunit monitormonth   
0          38       崙背      14       溫度    AMB_TEMP        ℃      2011/01  \
1          38       崙背       1     二氧化硫         SO2      ppb      2011/01   
2          38       崙背       5     氮氧化物         NOx      ppb      2011/01   
3          38       崙背      14       溫度    AMB_TEMP        ℃      2011/02   
4          38       崙背       5     氮氧化物         NOx      ppb      2011/02   
...       ...      ...     ...      ...         ...      ...          ...   
33332      85       大城       5     氮氧化物         NOx      ppb      2023/01   
33333      85       大城       1     二氧化硫         SO2      ppb      2023/01   
33334      85       大城       1     二氧化硫         SO2      ppb      2023/02   
33335      85       大城       5     氮氧化物         NOx      ppb      2023/02   
33336      85       大城      14       溫度    AMB_TEMP        ℃      2023/02   

       concentration areaname county  year month  
0              14.98   雲嘉南空品區    雲林縣  2011    01  
1               3.50   雲嘉南空品區    雲林縣  2011    01  
2              16.77   雲嘉南空品區    雲林縣  2011    01  
3              16.57   雲嘉南空品區    雲林縣  2011    02  
4              16.74   雲嘉南空品區    雲林縣  2011    02  
...              ...      ...    ...   ...   ...  
33332           5.70    中部空品區    彰化縣  2023    01  
33333           0.80    中部空品區    彰化縣  2023    01  
33334           0.90    中部空品區    彰化縣  2023    02  
33335           6.60    中部空品區    彰化縣  2023    02  
33336          16.90    中部空品區    彰化縣  2023    02  

[33337 rows x 12 columns]

將資料整理成視覺化需要的模樣

In [54]:
temp_df = merged_df[merged_df['itemengname'] == 'AMB_TEMP']
temp_df['temperature'] = temp_df['concentration']
temp_df = temp_df[['monitormonth', 'sitename', 'county', 'areaname', 'temperature']]
temp_df

C:\Users\s2568\AppData\Local\Temp\ipykernel_2164\2259091153.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



monitormonth sitename county areaname  temperature
0          2011/01       崙背    雲林縣   雲嘉南空品區        14.98
3          2011/02       崙背    雲林縣   雲嘉南空品區        16.57
8          2011/03       崙背    雲林縣   雲嘉南空品區        17.81
10         2011/04       崙背    雲林縣   雲嘉南空品區        22.61
14         2011/05       崙背    雲林縣   雲嘉南空品區        25.70
...            ...      ...    ...      ...          ...
33324      2022/10       大城    彰化縣    中部空品區        25.00
33327      2022/11       大城    彰化縣    中部空品區        23.40
33330      2022/12       大城    彰化縣    中部空品區        17.70
33331      2023/01       大城    彰化縣    中部空品區        16.60
33336      2023/02       大城    彰化縣    中部空品區        16.90

[10977 rows x 5 columns]

In [55]:
merged_df = merged_df[merged_df['itemengname'].isin(['NOx', 'SO2'])]
mergeKey = ['monitormonth', 'sitename', 'county', 'areaname']

merge = pd.merge(merged_df, temp_df, on=mergeKey)
merge


siteid sitename  itemid itemname itemengname itemunit monitormonth   
0          38       崙背       1     二氧化硫         SO2      ppb      2011/01  \
1          38       崙背       5     氮氧化物         NOx      ppb      2011/01   
2          38       崙背       5     氮氧化物         NOx      ppb      2011/02   
3          38       崙背       1     二氧化硫         SO2      ppb      2011/02   
4          38       崙背       1     二氧化硫         SO2      ppb      2011/03   
...       ...      ...     ...      ...         ...      ...          ...   
21949      85       大城       5     氮氧化物         NOx      ppb      2022/12   
21950      85       大城       5     氮氧化物         NOx      ppb      2023/01   
21951      85       大城       1     二氧化硫         SO2      ppb      2023/01   
21952      85       大城       1     二氧化硫         SO2      ppb      2023/02   
21953      85       大城       5     氮氧化物         NOx      ppb      2023/02   

       concentration areaname county  year month  temperature  
0               3.50   雲嘉南空品區    雲林縣  2011    01        14.98  
1              16.77   雲嘉南空品區    雲林縣  2011    01        14.98  
2              16.74   雲嘉南空品區    雲林縣  2011    02        16.57  
3               2.90   雲嘉南空品區    雲林縣  2011    02        16.57  
4               4.00   雲嘉南空品區    雲林縣  2011    03        17.81  
...              ...      ...    ...   ...   ...          ...  
21949           6.40    中部空品區    彰化縣  2022    12        17.70  
21950           5.70    中部空品區    彰化縣  2023    01        16.60  
21951           0.80    中部空品區    彰化縣  2023    01        16.60  
21952           0.90    中部空品區    彰化縣  2023    02        16.90  
21953           6.60    中部空品區    彰化縣  2023    02        16.90  

[21954 rows x 13 columns]

處理合併產生的空值

In [57]:
merge.dropna(subset=['temperature', 'concentration'], inplace=True) 
merge['temperature'].fillna(0, inplace=True) 
merge['concentration'].fillna(0, inplace=True)
merge


siteid sitename  itemid itemname itemengname itemunit monitormonth   
0          38       崙背       1     二氧化硫         SO2      ppb      2011/01  \
1          38       崙背       5     氮氧化物         NOx      ppb      2011/01   
2          38       崙背       5     氮氧化物         NOx      ppb      2011/02   
3          38       崙背       1     二氧化硫         SO2      ppb      2011/02   
4          38       崙背       1     二氧化硫         SO2      ppb      2011/03   
...       ...      ...     ...      ...         ...      ...          ...   
21949      85       大城       5     氮氧化物         NOx      ppb      2022/12   
21950      85       大城       5     氮氧化物         NOx      ppb      2023/01   
21951      85       大城       1     二氧化硫         SO2      ppb      2023/01   
21952      85       大城       1     二氧化硫         SO2      ppb      2023/02   
21953      85       大城       5     氮氧化物         NOx      ppb      2023/02   

       concentration areaname county  year month  temperature  
0               3.50   雲嘉南空品區    雲林縣  2011    01        14.98  
1              16.77   雲嘉南空品區    雲林縣  2011    01        14.98  
2              16.74   雲嘉南空品區    雲林縣  2011    02        16.57  
3               2.90   雲嘉南空品區    雲林縣  2011    02        16.57  
4               4.00   雲嘉南空品區    雲林縣  2011    03        17.81  
...              ...      ...    ...   ...   ...          ...  
21949           6.40    中部空品區    彰化縣  2022    12        17.70  
21950           5.70    中部空品區    彰化縣  2023    01        16.60  
21951           0.80    中部空品區    彰化縣  2023    01        16.60  
21952           0.90    中部空品區    彰化縣  2023    02        16.90  
21953           6.60    中部空品區    彰化縣  2023    02        16.90  

[21793 rows x 13 columns]

###  Tidy Data

In [58]:
columns_to_keep = ['monitormonth', 'sitename', 'county', 'areaname', 'temperature', 'itemengname', 'concentration']
tidy = merge.reindex(columns=columns_to_keep)
tidy

monitormonth sitename county areaname  temperature itemengname   
0          2011/01       崙背    雲林縣   雲嘉南空品區        14.98         SO2  \
1          2011/01       崙背    雲林縣   雲嘉南空品區        14.98         NOx   
2          2011/02       崙背    雲林縣   雲嘉南空品區        16.57         NOx   
3          2011/02       崙背    雲林縣   雲嘉南空品區        16.57         SO2   
4          2011/03       崙背    雲林縣   雲嘉南空品區        17.81         SO2   
...            ...      ...    ...      ...          ...         ...   
21949      2022/12       大城    彰化縣    中部空品區        17.70         NOx   
21950      2023/01       大城    彰化縣    中部空品區        16.60         NOx   
21951      2023/01       大城    彰化縣    中部空品區        16.60         SO2   
21952      2023/02       大城    彰化縣    中部空品區        16.90         SO2   
21953      2023/02       大城    彰化縣    中部空品區        16.90         NOx   

       concentration  
0               3.50  
1              16.77  
2              16.74  
3               2.90  
4               4.00  
...              ...  
21949           6.40  
21950           5.70  
21951           0.80  
21952           0.90  
21953           6.60  

[21793 rows x 7 columns]

## Plotly

In [59]:
import plotly.express as px

In [60]:
_min = tidy['concentration'].min()
_max = tidy['concentration'].max()

In [68]:
steps = []
for i in range(len(tidy)):
    step = dict(
        method = 'update',
        args = ['visible', [False] * len(tidy)],
    )
    step['args'][1][i] = True # Toggle i'th trace to "visible"
    steps.append(step)

sliders = [dict(
    active = 10,
    currentvalue = {"prefix": "Monitor Time: "},
    pad = {"t": 50},
    steps = steps
)]


In [75]:
fig2 = px.scatter(tidy, x='concentration', y="temperature", size='concentration',
	        color="itemengname", hover_name="sitename", log_x=True, size_max=60, 
            animation_frame='monitormonth', animation_group='sitename', range_x=[_min, _max], range_y=[0, 40],
            labels=dict(county='County', NOx='NOx (ppb)', temperature='Temperature'))

for trace in fig2.data:
    trace.marker.line.width = 1
    trace.marker.line.color = 'black'
# layout = dict(sliders=sliders)
# fig2 = dict(data=tidy, layout=layout)
# setting slider
# fig2.update_layout(
#     sliders=[
#         dict(
#             active=0,
#             currentvalue={"prefix": "Monitor Month : "},
#             pad={"b": 50}, # slider 在圖的位置
#             steps=[
#                 dict(label="2011", method="update", args=[{"visible": [True, False, False, False, False, False, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 1"}]),
#                 dict(label="2012", method="update", args=[{"visible": [False, True, False, False, False, False, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 2"}]),
#                 dict(label="2013", method="update", args=[{"visible": [False, False, True, False, False, False, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 3"}]),
#                 dict(label="2014", method="update", args=[{"visible": [False, False, False, True, False, False, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 4"}]),
#                 dict(label="2015", method="update", args=[{"visible": [False, False, False, False, True, False, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 5"}]),
#                 dict(label="2016", method="update", args=[{"visible": [False, False, False, False, False, True, False, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 6"}]),
#                 dict(label="2017", method="update", args=[{"visible": [False, False, False, False, False, False, True, False, False, False, False, False, False]}, {"title": "Scatter Plot - X: 7"}]),
#                 dict(label="2018", method="update", args=[{"visible": [False, False, False, False, False, False, False, True, False, False, False, False, False]}, {"title": "Scatter Plot - X: 8"}]),
#                 dict(label="2019", method="update", args=[{"visible": [False, False, False, False, False, False, False, False, True, False, False, False, False]}, {"title": "Scatter Plot - X: 9"}]),
#                 dict(label="2020", method="update", args=[{"visible": [False, False, False, False, False, False, False, False, False, True, False, False, False]}, {"title": "Scatter Plot - X: 10"}]),
#                 dict(label="2021", method="update", args=[{"visible": [False, False, False, False, False, False, False, False, False, False, True, False, False]}, {"title": "Scatter Plot - X: 11"}]),
#                 dict(label="2022", method="update", args=[{"visible": [False, False, False, False, False, False, False, False, False, False, False, True, False]}, {"title": "Scatter Plot - X: 12"}]),
#                 dict(label="2023", method="update", args=[{"visible": [False, False, False, False, False, False, False, False, False, False, False, False, True]}, {"title": "Scatter Plot - X: 13"}])                
#             ],
#             # steps=1  # 設定間隔為1
#         )
#     ]
# )

fig2.show()

In [76]:
import plotly.graph_objects as go


In [38]:
tidy[tidy['areaname'].isin(['高屛空品區'])]
fig3 = px.scatter(tidy, x='concentration', y="temperature", size='concentration',
	        color="itemengname", hover_name="sitename", log_x=True, size_max=60, 
            animation_frame='monitormonth', animation_group='sitename', range_x=[_min, _max], range_y=[0, 40],
            labels=dict(county='County', NOx='NOx (ppb)', temperature='Temperature'))

for trace in fig2.data:
    trace.marker.line.width = 1
    trace.marker.line.color = 'black'

fig3['layout']['sliders'][0]['currentvalue']['prefix']='Date: '
for i, date in enumerate(tidy['monitormonth'], start = 0):
    fig3['layout']['sliders'][0]['steps'][i]['label']=date

fig3.show()

In [15]:
tidy[tidy['areaname'].isin(['北部空品區'])]
fig3 = px.scatter(tidy, x='concentration', y="temperature", size='concentration',
	        color="itemengname", hover_name="sitename", log_x=True, size_max=60, 
            animation_frame='year', animation_group='sitename', range_x=[_min, _max], range_y=[0, 40],
            labels=dict(county='County', NOx='NOx (ppb)', temperature='Temperature'))

for trace in fig2.data:
    trace.marker.line.width = 1
    trace.marker.line.color = 'black'


fig3.show()